In [3]:
from keras.layers import Input, Dense, Reshape, Dropout, Activation
from keras.layers import LSTM, Bidirectional, BatchNormalization, ZeroPadding2D
from keras.models import Sequential, Model
from keras.layers.advanced_activations import LeakyReLU
from keras.optimizers import Adam
from keras.utils import np_utils

Using TensorFlow backend.


In [4]:
import tensorflow as tf
import pygame
import copy
import pretty_midi

pygame 1.9.6
Hello from the pygame community. https://www.pygame.org/contribute.html


In [5]:
import librosa
import mir_eval
import mir_eval.display
import IPython.display
import re
from mido  import MidiFile
from music21 import converter, instrument, note, chord, midi, stream, converter

import glob

In [6]:
from magenta.music.protobuf import music_pb2
import pretty_midi as pm
from magenta.music import note_sequence_io, midi_io
import six
#midi = pm.PrettyMIDI("rock.mid")
#mm.midi_to_sequence_proto(midi)

In [7]:
import numpy as np
import pandas as pd

import scipy.stats as stats
import matplotlib.pyplot as plot
import sklearn
import seaborn as sns


import pandas_profiling

#Path for the groove dataset

MIDI_PATH = "/home/mark/repos/Springboard/data/"
DATA_PATH = "/home/mark/repos/Springboard/data/info.csv"

groove_df = pd.read_csv(DATA_PATH)
groove_df

drummer                session                        id  \
0     drummer1  drummer1/eval_session   drummer1/eval_session/1   
1     drummer1  drummer1/eval_session  drummer1/eval_session/10   
2     drummer1  drummer1/eval_session   drummer1/eval_session/2   
3     drummer1  drummer1/eval_session   drummer1/eval_session/3   
4     drummer1  drummer1/eval_session   drummer1/eval_session/4   
...        ...                    ...                       ...   
1145  drummer2      drummer2/session2      drummer2/session2/11   
1146  drummer2      drummer2/session2      drummer2/session2/12   
1147  drummer2      drummer2/session2      drummer2/session2/13   
1148  drummer2      drummer2/session2      drummer2/session2/14   
1149  drummer2      drummer2/session2      drummer2/session2/15   

              style  bpm beat_type time_signature  \
0      funk/groove1  138      beat            4-4   
1     soul/groove10  102      beat            4-4   
2      funk/groove2  105      beat            4-4   
3      soul/groove3   86      beat            4-4   
4      soul/groove4   80      beat            4-4   
...             ...  ...       ...            ...   
1145           rock  130      beat            4-4   
1146           rock  130      beat            4-4   
1147           rock  130      beat            4-4   
1148           rock  130      beat            4-4   
1149           rock  130      beat            4-4   

                                          midi_filename  \
0     drummer1/eval_session/1_funk-groove1_138_beat_...   
1     drummer1/eval_session/10_soul-groove10_102_bea...   
2     drummer1/eval_session/2_funk-groove2_105_beat_...   
3     drummer1/eval_session/3_soul-groove3_86_beat_4...   
4     drummer1/eval_session/4_soul-groove4_80_beat_4...   
...                                                 ...   
1145         drummer2/session2/11_rock_130_beat_4-4.mid   
1146         drummer2/session2/12_rock_130_beat_4-4.mid   
1147         drummer2/session2/13_rock_130_beat_4-4.mid   
1148         drummer2/session2/14_rock_130_beat_4-4.mid   
1149         drummer2/session2/15_rock_130_beat_4-4.mid   

                                         audio_filename   duration  split  
0     drummer1/eval_session/1_funk-groove1_138_beat_...  27.872308   test  
1     drummer1/eval_session/10_soul-groove10_102_bea...  37.691158   test  
2     drummer1/eval_session/2_funk-groove2_105_beat_...  36.351218   test  
3     drummer1/eval_session/3_soul-groove3_86_beat_4...  44.716543   test  
4     drummer1/eval_session/4_soul-groove4_80_beat_4...  47.987500   test  
...                                                 ...        ...    ...  
1145                                                NaN   1.909613  train  
1146                                                NaN   1.808652  train  
1147                                                NaN   1.864421  train  
1148                                                NaN   1.875960  train  
1149                                                NaN   3.714419  train  

[1150 rows x 11 columns]

In [8]:
groove_df['style'].value_counts()

rock                 281
hiphop                91
funk                  77
punk                  58
neworleans/funk       48
                    ... 
jazz/klezmer           1
neworleans/chacha      1
rock/rockabilly        1
latin/reggaeton        1
rock/folk              1
Name: style, Length: 76, dtype: int64

In [9]:
pandas_profiling.ProfileReport(groove_df)

In [10]:
groove_df = groove_df[groove_df.beat_type != 'fill']
short = groove_df[groove_df.duration <=30]
short.count()
#43 < 5 seconds
#158 < 30 seconds
#261 < 1 minute

drummer           158
session           158
id                158
style             158
bpm               158
beat_type         158
time_signature    158
midi_filename     158
audio_filename    148
duration          158
split             158
dtype: int64

In [11]:
groove_df['style'].value_counts()

rock                         193
funk                          36
hiphop                        30
jazz                          24
afrobeat                      13
                            ... 
rock/halftime                  1
jazz/fast                      1
latin/venezuelan-merengue      1
rock/rockabilly                1
rock/folk                      1
Name: style, Length: 76, dtype: int64

In [12]:
groove_df = groove_df[groove_df.audio_filename.isna() == False]
groove_df.count()

drummer           444
session           444
id                444
style             444
bpm               444
beat_type         444
time_signature    444
midi_filename     444
audio_filename    444
duration          444
split             444
dtype: int64

In [13]:
#sample = groove_df.iloc[0]
#midi_sample = MIDI_PATH + sample.midi_filename
#audio_sample = MIDI_PATH + sample.audio_filename
#pm = pm.PrettyMIDI(midi_sample)

In [14]:
groove_df['style'].value_counts()

rock                       171
hiphop                      28
funk                        28
jazz                        24
jazz/swing                  11
                          ... 
funk/rock                    1
latin/reggaeton              1
latin/brazilian-frevo        1
latin/venezuelan-joropo      1
rock/folk                    1
Name: style, Length: 74, dtype: int64

In [15]:
groove_df['style'].value_counts()

rock                       171
hiphop                      28
funk                        28
jazz                        24
jazz/swing                  11
                          ... 
funk/rock                    1
latin/reggaeton              1
latin/brazilian-frevo        1
latin/venezuelan-joropo      1
rock/folk                    1
Name: style, Length: 74, dtype: int64

In [16]:
pandas_profiling.ProfileReport(groove_df)

In [17]:
single_styles = groove_df[groove_df['duration'] <= 20]
single_styles

drummer            session                    id            style  bpm  \
252   drummer1  drummer1/session1  drummer1/session1/76  jazz/mediumfast  180   
403   drummer1  drummer1/session2  drummer1/session2/33             punk  128   
404   drummer1  drummer1/session2  drummer1/session2/34             punk  128   
406   drummer1  drummer1/session2  drummer1/session2/36             punk  128   
407   drummer1  drummer1/session2  drummer1/session2/37             punk  128   
...        ...                ...                   ...              ...  ...   
1127  drummer9  drummer9/session1  drummer9/session1/30             rock   90   
1128  drummer9  drummer9/session1   drummer9/session1/4             rock  100   
1130  drummer9  drummer9/session1   drummer9/session1/6             rock  100   
1132  drummer9  drummer9/session1   drummer9/session1/8             rock  100   
1133  drummer9  drummer9/session1   drummer9/session1/9             rock  100   

     beat_type time_signature  \
252       beat            4-4   
403       beat            4-4   
404       beat            4-4   
406       beat            4-4   
407       beat            4-4   
...        ...            ...   
1127      beat            4-4   
1128      beat            4-4   
1130      beat            4-4   
1132      beat            4-4   
1133      beat            4-4   

                                          midi_filename  \
252   drummer1/session1/76_jazz-mediumfast_180_beat_...   
403          drummer1/session2/33_punk_128_beat_4-4.mid   
404          drummer1/session2/34_punk_128_beat_4-4.mid   
406          drummer1/session2/36_punk_128_beat_4-4.mid   
407          drummer1/session2/37_punk_128_beat_4-4.mid   
...                                                 ...   
1127          drummer9/session1/30_rock_90_beat_4-4.mid   
1128          drummer9/session1/4_rock_100_beat_4-4.mid   
1130          drummer9/session1/6_rock_100_beat_4-4.mid   
1132          drummer9/session1/8_rock_100_beat_4-4.mid   
1133          drummer9/session1/9_rock_100_beat_4-4.mid   

                                         audio_filename   duration  split  
252   drummer1/session1/76_jazz-mediumfast_180_beat_...   7.315270  train  
403          drummer1/session2/33_punk_128_beat_4-4.wav   3.811523  train  
404          drummer1/session2/34_punk_128_beat_4-4.wav   7.115234  train  
406          drummer1/session2/36_punk_128_beat_4-4.wav   7.198242  train  
407          drummer1/session2/37_punk_128_beat_4-4.wav   1.821289  train  
...                                                 ...        ...    ...  
1127          drummer9/session1/30_rock_90_beat_4-4.wav  18.641676  train  
1128          drummer9/session1/4_rock_100_beat_4-4.wav   9.663750  train  
1130          drummer9/session1/6_rock_100_beat_4-4.wav   4.748750  train  
1132          drummer9/session1/8_rock_100_beat_4-4.wav  11.208750  train  
1133          drummer9/session1/9_rock_100_beat_4-4.wav   9.071250  train  

[109 rows x 11 columns]

In [18]:
styles = groove_df['style'].value_counts()
style_durations = pd.DataFrame(columns=['style','max','min','sum'])
for s in styles.index:
    style_df = groove_df.query('style=="'+s+'"')
    style_durations = style_durations.append({'style': s, 'max': style_df['duration'].max(), 
                                             'min': style_df['duration'].min(), 'sum': style_df['duration'].sum()},
                                             ignore_index=True)
#print(style_df.count())
style_durations.sort_values(by=['sum'], ascending='True')

style         max         min          sum
58            latin/merengue   18.304597   18.304597    18.304597
62              jazz/klezmer   37.595410   37.595410    37.595410
51  latin/venezuelan-sangueo   80.779648   80.779648    80.779648
70           latin/reggaeton   87.784634   87.784634    87.784634
59                 jazz/fast  105.048858  105.048858   105.048858
..                       ...         ...         ...          ...
40     latin/brazilian-bossa  611.564048  582.125068  1193.689116
3                       jazz  183.415349    3.196875  1383.800351
1                     hiphop  191.755389    4.361367  1849.707697
2                       funk  297.670000    4.482500  3206.277720
0                       rock  305.406445    1.290000  8478.819136

[74 rows x 4 columns]

In [19]:
#Method 1: Add the multi-style to the first substyle.
test_df = groove_df
for s in styles.index:
    if '/' in s:
        print(s)
        style_a,style_b = s.split('/')
        print(s.split('/'))
        if style_a in styles.index:
            print(style_a)
            split_style = groove_df.query('style=="'+s+'"')
            test_df = test_df.replace({'style':{s:style_a}})
            #groove_df = groove_df.replace({'style':{s:style_a}})
        if style_b in styles.index:
            print(style_b)
            split_style = groove_df.query('style=="'+s+'"')
            test_df = test_df.replace({'style':{s:style_b}})
            groove_df = groove_df.replace({'style':{s:style_b}})
#groove_df['style'].value_counts()
test_df['style'].value_counts()

jazz/swing
['jazz', 'swing']
jazz
neworleans/funk
['neworleans', 'funk']
funk
latin/brazilian-samba
['latin', 'brazilian-samba']
latin
funk/groove5
['funk', 'groove5']
funk
rock/groove8
['rock', 'groove8']
rock
soul/motown
['soul', 'motown']
soul
soul/groove4
['soul', 'groove4']
soul
pop/groove7
['pop', 'groove7']
pop
soul/groove9
['soul', 'groove9']
soul
latin/brazilian
['latin', 'brazilian']
latin
hiphop/groove6
['hiphop', 'groove6']
hiphop
funk/groove2
['funk', 'groove2']
funk
soul/groove3
['soul', 'groove3']
soul
jazz/fusion
['jazz', 'fusion']
jazz
blues/shuffle
['blues', 'shuffle']
soul/groove10
['soul', 'groove10']
soul
funk/groove1
['funk', 'groove1']
funk
latin/brazilian-baiao
['latin', 'brazilian-baiao']
latin
latin/chacarera
['latin', 'chacarera']
latin
latin/brazilian-songo
['latin', 'brazilian-songo']
latin
pop/soft
['pop', 'soft']
pop
rock/shuffle
['rock', 'shuffle']
rock
latin/brazilian-sambareggae
['latin', 'brazilian-sambareggae']
latin
neworleans/secondline
['neworlean

rock                     186
funk                      51
jazz                      50
latin                     42
hiphop                    32
soul                      28
pop                       15
afrocuban                  7
punk                       7
blues/shuffle              4
reggae                     4
afrobeat                   4
dance/disco                3
neworleans/secondline      3
country                    2
dance/breakbeat            2
neworleans/chacha          1
gospel                     1
neworleans/shuffle         1
middleeastern              1
Name: style, dtype: int64

In [20]:
#styles = groove_df['style'].value_counts()
styles = test_df['style'].value_counts()
style_durations = pd.DataFrame(columns=['style','max','min','sum'])
for s in styles.index:
    style_df = groove_df.query('style=="'+s+'"')
    style_durations = style_durations.append({'style': s, 'max': style_df['duration'].max(), 
                                             'min': style_df['duration'].min(), 'sum': int(style_df['duration'].sum())},
                                             ignore_index=True)
#print(style_df.count())
style_durations.sort_values(by=['sum'], ascending='True')



style         max         min   sum
16      neworleans/chacha  115.856863  115.856863   115
18     neworleans/shuffle  130.782434  130.782434   130
17                 gospel  139.527083  139.527083   139
15        dance/breakbeat  108.466858   56.392619   164
19          middleeastern  226.604932  226.604932   226
9           blues/shuffle  269.532878    3.564364   288
14                country  154.966071  144.700364   299
6                     pop   85.468267   12.709268   313
8                    punk  203.251899    1.821289   484
12            dance/disco  225.941667   58.050000   491
13  neworleans/secondline  271.979975   94.731861   502
10                 reggae  206.679119  114.703411   507
5                    soul  132.277344   27.389306   535
7               afrocuban  226.857422  134.383199   584
11               afrobeat  257.856435  150.822298   796
3                   latin  196.199684  124.891250   801
2                    jazz  183.415349    3.196875  1383
4                  hiphop  191.755389    4.361367  1849
1                    funk  297.670000    4.482500  4206
0                    rock  305.406445    1.290000  8598

In [21]:
styles_removed = style_durations[style_durations['sum'] < 100]
print(styles_removed)
#groove_df = groove_df[groove_df.style]

Empty DataFrame
Columns: [style, max, min, sum]
Index: []


In [22]:
#Generates MIDI list for each genre
genre_midi_list = {}
for s in styles.index:
    style_df = groove_df.query('style=="'+s+'"')
    genre_midi_list[s] = style_df.midi_filename.tolist()


In [23]:


def create_midi_old(prediction_output):
    offset = 0
    output_notes = []
    
    for item in prediction_output:
        print(item)
        pattern = item[0]
        if ('.' in pattern) or pattern.isdigit():
            notes_in_chord = pattern.split('.')
            notes = []
            for current_note in notes_in_chord:
                new_note = note.Note(int(current_note))
                new_note.storedInstrument = instrument.Piano()
                notes.append(new_note)
            new_chord = chord.Chord(notes)
            new_chord.offset = offset
            output_notes.append(new_chord)
        else:
            new_note = note.Note(pattern)
            new_note.offset = offset
            new_note.storedInstrument = instrument.Piano()
            output_notes.append(new_note)
        offset += 0.5
    print(output_notes)
    midi_stream = stream.Stream(output_notes)
    midi_stream.write('midi', fp='/home/mark/repos/Springboard/test_output.mid')

In [24]:
def create_midi(prediction_output):
    offset = 0
    output_notes = []
    
    pm = midi.percussion.PercussionMapper()

    for item in prediction_output:
        print(item)
        pattern = item[0]
        if ('.' in pattern) or pattern.isdigit():
            notes_in_chord = pattern.split('.')
            notes = []
            for current_note in notes_in_chord:
                new_note = note.Note(int(current_note))
                try:
                    print(type(pm.midiPitchToInstrument(new_note.pitch)))
                    new_note.storedInstrument = pm.midiPitchToInstrument(new_note.pitch)
                    print(new_note.storedInstrument)
                    notes.append(new_note)
                except:
                    print('aaaa')
                    pass
            new_chord = chord.Chord(notes)
            new_chord.offset = offset
            output_notes.append(new_chord)
        else:
            new_note = note.Note(pattern)
            #print(new_note.storedInstrument)
            new_note.offset = offset
            try:
                print(type(pm.midiPitchToInstrument(new_note.pitch)))
                new_note.storedInstrument = pm.midiPitchToInstrument(new_note.pitch)
                output_notes.append(new_note)
            except:
                print('bbbb')
                pass
        offset += 0.5
    print(output_notes)
    midi_stream = stream.Stream()
    midi_stream.append(output_notes)
    midi_stream.write('midi', fp='/home/mark/repos/Springboard/test_output.mid')

In [25]:

class drum_gan():
    
    def __init__(self, rows):
        
        self.seq_length = rows
        self.seq_shape = (self.seq_length, 79)
        self.latent_dim = 1000
        self.disc_loss = []
        self.gen_loss =[]
        
        self.genre = 'rock'
        optimizer = Adam(0.0002, 0.5)
        
        self.discriminator = self.create_discriminator()
        self.discriminator.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])
        
        self.generator = self.create_generator()
        
        #Generator takes in noise as input and generated sequence
        z = Input(shape=(self.latent_dim,))
        seq = self.generator(z)
        
        #Only train the generator for the combined model
        self.discriminator.trainable = False
        
        #Determine the validity of the generated sequence as an input
        valid = self.discriminator(seq)
        
        #Combined model takes noise as input, generates sequence and then determines validity 
        self.combined = Model(z, valid)
        self.combined.compile(loss='binary_crossentropy', optimizer=optimizer)

    def create_discriminator(self):
        model = Sequential()
        model.add(LSTM(512, input_shape=self.seq_shape, return_sequences=True))
        model.add(Bidirectional(LSTM(512)))
        model.add(Dropout(0.4))
        model.add(Dense(512))
        model.add(LeakyReLU(alpha=0.2))
        model.add(Dropout(0.4))
        model.add(Dense(256))
        model.add(Dropout(0.4))
        model.add(LeakyReLU(alpha=0.2))
        model.add(Dense(100, activation='sigmoid'))
        model.summary()

        seq = Input(shape=self.seq_shape)
        validity = model(seq)

        return Model(seq, validity)

    def create_generator(self):
        model = Sequential()
        model.add(Dense(256, input_dim=self.latent_dim))
        model.add(LeakyReLU(alpha=0.2))
        model.add(BatchNormalization(momentum=0.8))
        #model.add(Dropout(0.2))
        model.add(Dense(512))
        model.add(LeakyReLU(alpha=0.2))
        model.add(BatchNormalization(momentum=0.8))
        #model.add(Dropout(0.2))
        model.add(Dense(1024))
        model.add(LeakyReLU(alpha=0.2))
        model.add(BatchNormalization(momentum=0.8))
        #model.add(Dropout(0.2))
        model.add(Dense(np.prod(self.seq_shape),activation='tanh'))
        model.add(Reshape(self.seq_shape))
        #model.add(Dropout(0.2))
        model.summary()

        noise = Input(shape=(self.latent_dim,))
        seq = model(noise)

        return Model(noise, seq)
    
    #TODO: Create function for separating dataset into genres to get rid of genre_dataset in function
    def train(self, genre_dataset, epochs, batch_size=128, sample_interval=50):
        
        #Load the dataset
        
        #notes = midi_to_notes(genre_dataset)
        #n_vocab = len(set(notes))
        
        #UPDATED:
        notes = get_notes(genre_dataset)
        n_vocab = len(notes)
        
        X_train, y_train = prepare_sequences(notes, n_vocab)
        
        real = np.ones((batch_size,100))
        fake = np.zeros((batch_size,100))
        #Begin looping through the number of epochs
        for epoch in range(epochs):
            
            # ********* Train discriminator on random batch of inputs *********
            idx = np.random.randint(0, X_train.shape[0],batch_size)
            seqs = X_train[idx]
            
            
            noise = np.random.normal(0, 100, (batch_size, self.latent_dim))
            
            #Generate full batch of sequences
            gen_seq = self.generator.predict(noise)
            
            d_loss_real = self.discriminator.train_on_batch(seqs, real)
            d_loss_fake = self.discriminator.train_on_batch(gen_seq, fake)
            
            d_loss = 0.5 * np.add(d_loss_real, d_loss_fake)
            
            # ********* Train generator using the combined model *********
            # Generate noise to trick discriminator to thinking they are valid
            noise = np.random.normal(0, 1, (batch_size, self.latent_dim))
            
            valid_y = np.array([1] * batch_size)
            
            #g_loss = self.combined.train_on_batch(noise, valid_y)
            g_loss = self.combined.train_on_batch(noise, real)
            #Plot Progress
            #print("%d [D loss: %f, acc: %.2f%%] [G loss: %f]" % (epoch, d_loss[0], 100*d_loss[1], g_loss))
            #print("%d [D loss: %f, acc: %.2f%%] [G loss: %f]" % (epoch, d_loss, 100*d_loss, g_loss))
            
    #Creates a new drumtrack from the notes from out dataset
    def generate(self, input_notes):
        notes = input_notes
        
        #Retrieve all pitch names
        pitchnames = sorted(set(item for item in notes))

        #Create a dictionary to map pitches to integers
        int_to_note = dict((number, note) for number, note in enumerate(pitchnames))
        
        noise = np.random.normal(0, 1, (1, self.latent_dim))
        
        #Call generator to make predictions based on the noise
        predictions = self.generator.predict(noise)
        
        pred_notes = [x*47+47 for x in predictions[0]]
        pred_notes = [int_to_note[int(x)] for x in pred_notes]
        print(pred_notes)
        #Create Midi fiFle
        create_midi(pred_notes)

In [26]:
#def retrieve_tracks(genre):
    

In [27]:
def midi_to_note_sequence(midi_list):
    notes = []
    for file in midi_list:
        notes_to_parse = midi_io.midi_file_to_note_sequence(MIDI_PATH + file)
        
        #ONLY WORKING WITH DRUM TRACKS ONLY
        #notes_to_parse = midi_io.note_sequence_to_pretty_midi(midi_retrieved)
        #print(notes_to_parse.notes)
        for element in notes_to_parse.notes:
            notes.append(element)
        
    return notes

In [28]:
def midi_to_notes(midi_list):
    """Retrieves all notes from midi files passed from midi list"""
    
    notes = []
    for file in midi_list:
        midi_retrieved = converter.parse(MIDI_PATH + file)            
        
        print("Parsing %s", midi_retrieved)
        
        notes_to_parse = None
        
        try:#file has instrument parts
            s2 = instrument.partitionByInstrument(midi_retrieved)
            print(s2.parts)
            notes_to_parse = s2.parts[0].recurse()
        
        except:#File notes have flat structure
            notes_to_parse = midi_retrieved.flat.notes
        
        for element in notes_to_parse:
            if isinstance(element, note.Note):
                notes.append(str(element.pitch))
            elif isinstance(element, chord.Chord):
                notes.append('.'.join(str(n) for n in element.normalOrder))
        
    return notes

In [29]:
def midi_to_notes_old(midi_list):
    """Retrieves all notes from midi files passed from midi list"""
    
    pm = midi.percussion.PercussionMapper()
    
    notes = []
    for file in midi_list:
        midi_retrieved = converter.parse(MIDI_PATH + file)
        
        print("Parsing %s", file)
        
        notes_to_parse = None
        
        try:#file has instrument parts
            s2 = instrument.partitionByInstrument(midi_retrieved)
            print(s2.parts)
            notes_to_parse = s2.parts[0].recurse()
        
        except:#File notes have flat structure
            notes_to_parse = midi_retrieved.flat.notes
        
        for element in notes_to_parse:
            if isinstance(element, note.Note):
                #print("NOTE")
                print(element)
                #print(element.pitch.midi)
                try:
                    pm.midiPitchToInstrument(element.pitch)
                    element.storedInstrument = pm.midiPitchToInstrument(element.pitch)
                    #print(pm.midiPitchToInstrument(element.pitch.midi))
                    notes.append(str(element.pitch))
                    #print("**********")
                except:
                    pass
                    #print("EEEEE")
                    #print("**********")
            elif isinstance(element, chord.Chord):
                #print("CHORD")
                #print(element)
                chord_notes = ''
                #for n, n_order in zip(element,element.normalOrder):
                    #print(n)
                    #print(n_order)
                    #try:
                        #pm.midiPitchToInstrument(n.pitch.midi)
                        #chord_notes = chord_notes + '.'.join(str(n_order))
                        #print(pm.midiPitchToInstrument(n.pitch.midi))
                    #except:
                        #print("RRRRR")
                #notes.append(chord_notes)
                notes.append('.'.join(str(n) for n in element.normalOrder))
                #print("**********")
        
    return notes

In [30]:
def prepare_sequences(notes, n_vocab):
    sequence_length = 100
    network_input = []
    network_output = []

    network_input = [notes[i][t:t+sequence_length] for i in range(len(notes)) 
                     for t in range(len(notes[i])-sequence_length)]
    
    network_output = [notes[i][t+ sequence_length] for i in range(len(notes)) 
                      for t in range(len(notes[i])-sequence_length)]

    sequence_in = np.asarray(network_input)
    sequence_out = np.asarray(network_output)

    #print("X_train.shape:", sequence_in.shape)
    #print("y_train.shape:", sequence_out.shape)
    return (sequence_in, sequence_out)

In [31]:
def prepare_sequences_test(notes, n_vocab):
    sequence_length = 100
    network_input = []
    network_output = []
    sequence_in = []
    sequence_out = []
    print("Inputs")
    for i in range(len(notes)):
        print(i)
        for t in range(len(notes[i])-sequence_length):
            network_input = notes[i][t:t+sequence_length]
            network_output = notes[i][t+ sequence_length]
        sequence_in.append(c for c in network_input)
        sequence_out.append(network_output)
    #sequence_in = np.asarray(network_input)
    print("input")
    print(len(network_input))
    print("output")
    print(len(network_output))
    print("seq_in")
    print(sequence_in)
    print("seq_out")
    print(sequence_out)   
    #sequence_out = np.asarray(network_output)

    print("X_train.shape:", sequence_in.shape)
    print("y_train.shape:", sequence_out.shape)
    return (sequence_in, sequence_out)

In [32]:
def prepare_sequences_old(notes,n_vocab):
    """ Prepare the sequences used by the Neural Network"""
    sequence_length = 100
    
    #Retrieve all pitch names
    pitchnames = sorted(set(item for item in notes))
    
    #Create a dictionary to map pitches to integers
    note_to_int = dict((note, number) for number, note in enumerate(pitchnames))
    
    input_network = []
    output_network = []
    #Create the input sequences and the corresponding outputs
    for i in range(0, len(notes) - sequence_length, 1):
        input_sequence = notes[i:i+sequence_length]
        output_sequence = notes[i+sequence_length]
        input_network.append([note_to_int[c] for c in input_sequence])
        output_network.append(note_to_int[output_sequence])
    print(len(output_sequence))
    print(len(input_sequence))
    print(len(output_network))
    print(len(input_network))
    n_patterns = len(input_network)
    
    #Reshape input into compatible format for LSTM layers
    input_network = np.reshape(input_network, (n_patterns, sequence_length, 1))

    #Normalize input
    input_network = (input_network - (float(n_vocab) / 2)) / (float(n_vocab) / 2)
    output_network = np_utils.to_categorical(output_network)
    
    return(input_network, output_network)
    #Why did you implement a conditional statement with input/output or input/normalized??

In [33]:
#midi_retrieved = converter.parse(MIDI_PATH + "drummer1/session2/6_rock_102_beat_3-4.mid")

#n_to_p = midi_io.midi_file_to_note_sequence(MIDI_PATH + "drummer1/session2/6_rock_102_beat_3-4.mid")
#midi_retrieved = midi_io.note_sequence_to_pretty_midi(n_to_p)
#midi_stream = stream.Stream(midi_retrieved)
#midi_stream = stream.Stream(midi_retrieved)
#ch = midi.translate.channelInstrumentData(midi_stream) 
#mf = midi.translate.streamToMidiFile(midi_retrieved)
#mf.open('/home/mark/repos/Springboard/test_output_1.mid', 'wb')
#mf.write()
#mf.close()

#print(ch)
#midi_stream.write('midi', fp='/home/mark/repos/Springboard/test_output_1.mid')

In [34]:
n_x = 79
max_T_x = 1000
sequence_length = 20
T_y_generated = 200

In [35]:
def get_notes(midi_list):
    """ Get all the notes and chords from the midi files """
    notes = []

    for file in midi_list:
        midi_data = pretty_midi.PrettyMIDI(MIDI_PATH + file)

        #print("Parsing %s" % file)

        note_l = [note.pitch for note in midi_data.instruments[0].notes]
        # convert to one-hot-encoding
        T_x = len(note_l)
        if T_x > max_T_x:
            T_x = max_T_x
        X_ohe = np.zeros((T_x, n_x))
        for t in range(T_x): 
             X_ohe[t, note_l[t]-1] = 1
        # add to the list  
        notes.append(X_ohe)
    return notes

In [36]:
#TEST AREA

#frames per sec is something to figure out

#rock_notes = get_notes(genre_midi_list['rock'])
#rock_vocab = len(rock_notes)
#network_input,network_output = prepare_sequences(rock_notes, rock_vocab)

#print(network_input)
#print(network_output)
#pitch_from_instrument = pm.midiInstrumentToPitch(s2)

#print(pitch_from_instrument)

#rock_list = midi_to_note_sequence(genre_midi_list['rock'])
#rock_notes = midi_to_notes(genre_midi_list['rock'])
#rock_vocab = len(set(rock_notes))
#print(rock_vocab)
#rock_notes = midi_to_notes(["drummer1/session2/6_rock_102_beat_3-4.mid"])
#rock_notes = midi_to_notes_old(["drummer1/session2/6_rock_102_beat_3-4.mid"])
#X_train, y_train = prepare_sequences_old(rock_notes, rock_vocab)
#print(X_train)
#print(y_train)
#rock_notes = midi_to_note_sequence(["drummer1/session2/6_rock_102_beat_3-4.mid"])
#rock_vocab = len(set(rock_notes))
#rock_vocab = len(set(rock_notes))
#print(rock_notes)
#print(rock_vocab)
#print(rock_vocab)
#pandas_profiling.ProfileReport(rock_list)

In [ ]:
gan = drum_gan(rows=100)
gan.train(genre_dataset=genre_midi_list['rock'], epochs=15, batch_size=10, sample_interval=1)

W0329 19:04:55.775421 140579605010240 module_wrapper.py:139] From /home/mark/.local/lib/python3.6/site-packages/keras/backend/tensorflow_backend.py:74: The name tf.get_default_graph is deprecated. Please use tf.compat.v1.get_default_graph instead.

W0329 19:04:55.778444 140579605010240 module_wrapper.py:139] From /home/mark/.local/lib/python3.6/site-packages/keras/backend/tensorflow_backend.py:517: The name tf.placeholder is deprecated. Please use tf.compat.v1.placeholder instead.

W0329 19:04:55.783198 140579605010240 module_wrapper.py:139] From /home/mark/.local/lib/python3.6/site-packages/keras/backend/tensorflow_backend.py:4138: The name tf.random_uniform is deprecated. Please use tf.random.uniform instead.

W0329 19:04:58.767265 140579605010240 module_wrapper.py:139] From /home/mark/.local/lib/python3.6/site-packages/keras/backend/tensorflow_backend.py:133: The name tf.placeholder_with_default is deprecated. Please use tf.compat.v1.placeholder_with_default instead.

W0329 19:04:58

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
lstm_1 (LSTM)                (None, 100, 512)          1212416   
_________________________________________________________________
bidirectional_1 (Bidirection (None, 1024)              4198400   
_________________________________________________________________
dropout_1 (Dropout)          (None, 1024)              0         
_________________________________________________________________
dense_1 (Dense)              (None, 512)               524800    
_________________________________________________________________
leaky_re_lu_1 (LeakyReLU)    (None, 512)               0         
_________________________________________________________________
dropout_2 (Dropout)          (None, 512)               0         
_________________________________________________________________
dense_2 (Dense)              (None, 256)               131328    
__________

W0329 19:05:00.138887 140579605010240 module_wrapper.py:139] From /home/mark/.local/lib/python3.6/site-packages/keras/optimizers.py:790: The name tf.train.Optimizer is deprecated. Please use tf.compat.v1.train.Optimizer instead.

W0329 19:05:00.146944 140579605010240 module_wrapper.py:139] From /home/mark/.local/lib/python3.6/site-packages/keras/backend/tensorflow_backend.py:3376: The name tf.log is deprecated. Please use tf.math.log instead.

W0329 19:05:00.155446 140579605010240 deprecation.py:323] From /home/mark/.conda/envs/Springboard/lib/python3.6/site-packages/tensorflow_core/python/ops/nn_impl.py:183: where (from tensorflow.python.ops.array_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_4 (Dense)              (None, 256)               256256    
_________________________________________________________________
leaky_re_lu_3 (LeakyReLU)    (None, 256)               0         
_________________________________________________________________
batch_normalization_1 (Batch (None, 256)               1024      
_________________________________________________________________
dense_5 (Dense)              (None, 512)               131584    
_________________________________________________________________
leaky_re_lu_4 (LeakyReLU)    (None, 512)               0         
_________________________________________________________________
batch_normalization_2 (Batch (None, 512)               2048      
_________________________________________________________________
dense_6 (Dense)              (None, 1024)              525312    
__________

W0329 19:05:18.349824 140579605010240 module_wrapper.py:139] From /home/mark/.local/lib/python3.6/site-packages/keras/backend/tensorflow_backend.py:2741: The name tf.Session is deprecated. Please use tf.compat.v1.Session instead.

W0329 19:05:20.681978 140579605010240 module_wrapper.py:139] From /home/mark/.local/lib/python3.6/site-packages/keras/backend/tensorflow_backend.py:174: The name tf.get_default_session is deprecated. Please use tf.compat.v1.get_default_session instead.

W0329 19:05:20.685521 140579605010240 module_wrapper.py:139] From /home/mark/.local/lib/python3.6/site-packages/keras/backend/tensorflow_backend.py:181: The name tf.ConfigProto is deprecated. Please use tf.compat.v1.ConfigProto instead.

W0329 19:05:25.543621 140579605010240 module_wrapper.py:139] From /home/mark/.local/lib/python3.6/site-packages/keras/backend/tensorflow_backend.py:190: The name tf.global_variables is deprecated. Please use tf.compat.v1.global_variables instead.

W0329 19:05:25.601920 1405796

In [37]:
#notes = midi_to_notes(genre_midi_list['rock'])
#gan.generate(notes)

In [38]:
pygame.init()

(6, 0)

In [39]:
#pygame.mixer.music.load('/home/mark/repos/Springboard/test_output.mid')
#pygame.mixer.music.play(0)
#while pygame.mixer.music.get_busy():
#    pygame.time.Clock().tick()

In [40]:
m = converter.parse('/home/mark/repos/Springboard/test_output.mid')
m.show('midi')

In [41]:
'''
def to_piano_roll(midi):
    """Convert MIDI file to a 2D NumPy ndarray (notes, timesteps)."""
    print (midi)
    notes = 127
    tempo = 500000  # Assume same default tempo and 4/4 for all MIDI files.
    seconds_per_beat = tempo / 1000000.0
    seconds_per_tick = seconds_per_beat / midi.ticks_per_beat
    velocities = np.zeros(notes)
    sequence = []
    for m in midi:
        ticks = int(np.round(m.time / seconds_per_tick))
        ls = [velocities.copy()] * ticks
        sequence.extend(ls)
        if m.type == 'note_on':
            velocities[m.note] = m.velocity
        #elif m.type == 'note_off':
        #    print(m.type)
        #    velocities[m.note] = 0
        else:
            continue
    #print (sequence)
    piano_roll = np.array(sequence).T
    return piano_roll

piano_roll = to_piano_roll(MidiFile('/home/mark/repos/Springboard/groove-v1.0.0-midionly/groove/drummer3/session1/4_rock_105_beat_4-4.mid'))
print (piano_roll)
#import numpy
np.where(piano_roll != 0.)
#lr.display.specshow(piano_roll)

def midi_to_notes_p(midi_list):
    """Retrieves all notes from midi files passed from midi list"""
    pm = midi.percussion.PercussionMapper()
    
    notes = []
    for file in midi_list:
        midi_retrieved = converter.parse(MIDI_PATH + file)
        
        print("Parsing %s", file)
        
        notes_to_parse = None
        
        try:#file has instrument parts
            s2 = instrument.partitionByInstrument(midi_retrieved)
            print(s2.parts)
            notes_to_parse = s2.parts[0].recurse()
        
        except:#File notes have flat structure
            notes_to_parse = midi_retrieved.flat.notes
        
        for element in notes_to_parse:
            if isinstance(element, note.Note):
                notes.append(str(element.pitch))
            elif isinstance(element, chord.Chord):
                notes.append('.'.join(str(n) for n in element.normalOrder))
        
    return notes
'''

'\ndef to_piano_roll(midi):\n    """Convert MIDI file to a 2D NumPy ndarray (notes, timesteps)."""\n    print (midi)\n    notes = 127\n    tempo = 500000  # Assume same default tempo and 4/4 for all MIDI files.\n    seconds_per_beat = tempo / 1000000.0\n    seconds_per_tick = seconds_per_beat / midi.ticks_per_beat\n    velocities = np.zeros(notes)\n    sequence = []\n    for m in midi:\n        ticks = int(np.round(m.time / seconds_per_tick))\n        ls = [velocities.copy()] * ticks\n        sequence.extend(ls)\n        if m.type == \'note_on\':\n            velocities[m.note] = m.velocity\n        #elif m.type == \'note_off\':\n        #    print(m.type)\n        #    velocities[m.note] = 0\n        else:\n            continue\n    #print (sequence)\n    piano_roll = np.array(sequence).T\n    return piano_roll\n\npiano_roll = to_piano_roll(MidiFile(\'/home/mark/repos/Springboard/groove-v1.0.0-midionly/groove/drummer3/session1/4_rock_105_beat_4-4.mid\'))\nprint (piano_roll)\n#import n